# Interactive pixel to Spectrum x DTM Analysis in Attribute Space

Fonctionnel, mériterais une réécriture :p

In [1]:
import rasterio as rio
import sap
import matplotlib as mpl
from matplotlib import pyplot as plt
import inspect
import ipywidgets as ipw
import higra as hg
import numpy as np
from pathlib import Path

plt.style.use('dark_background')
plt.set_cmap('plasma')
plt.close()

## Load dataset

dtm = rio.open('data/dsm_vox_50cm_tile_-12_0.tif').read()[0]#[-500:,-500:].copy()
dtm.shape

In [2]:
data_dir = Path('data')
tiles = list(data_dir.glob('**/*.tif'))

print('{} tiles loaded.'.format(len(tiles)))

918 tiles loaded.


In [65]:
lidar_features = list(set([str(x.stem).split('_vox_')[0] for x in tiles]))
tile_names = list(set(['_'.join(str(x.stem).split('_')[-2:]) for x in tiles]))

def get_tile(feature, name):
    return list(data_dir.glob('**/{}_vox_50cm_tile_{}.tif'.format(feature, name)))[0]



## Setup utils

In [4]:
def ui8_clip(x, vmin=None, vmax=None):
    vmin = vmin if vmin else np.nanmin(x)
    vmax = vmax if vmax else np.nanmax(x)
    
    ui8 = ((np.clip(x, vmin, vmax) - vmin) / (vmax - vmin) * 255).astype(np.uint8)
    
    return np.ma.array(ui8, mask=np.isnan(x))

def hillshades(x):
    hs = np.zeros_like(x) 
    hs[:-1,:-1] = x[:-1,:-1] - x[1:,1:]
    return hs

from sap.spectra import get_bins

def spectrum2d(tree, x_attribute, y_attribute, x_count=100, y_count=100, 
               x_log=False, y_log=False, weighted=True, normalized=True,
               node_mask=None):
    x = tree.get_attribute(x_attribute)
    y = tree.get_attribute(y_attribute)

    bins = (get_bins(x, x_count, 'geo' if x_log else 'lin'),
            get_bins(y, y_count, 'geo' if y_log else 'lin'))

    weights = tree.get_attribute('area') if weighted else None
    weights = weights / tree._image.size if normalized and weighted else weights

    s, xedges, yedges = np.histogram2d(x[node_mask].ravel(), y[node_mask].ravel(),
                                       bins=bins, density=None, weights=weights[node_mask].ravel())

    return s, xedges, yedges, x_log, y_log

def pixel_to_node(tree, mask):
    """Compute the node mask from the pixel mask."""
    node_mask = hg.accumulate_and_min_sequential(tree._tree, 
                                                 np.ones(tree._tree.num_vertices(), dtype=np.uint8), 
                                                 mask.ravel(), 
                                                 hg.Accumulators.min).astype(np.bool)
    return node_mask

#dtm_hs = ui8_clip(hillshades(dtm), -1, 1)
#cm_hud = mpl.colors.LinearSegmentedColormap.from_list('GreenHUD', [(0.,0.,0.,0.), (0.,1.,0.,1.)], 256)
#alpha = ((dtm_hs.astype(float) - 127) / 127) ** 2 * .4
#cX, cY = np.meshgrid(np.arange(dtm.shape[1]), np.arange(dtm.shape[0]))
#kwargs = {}
#kwargs['vmin'], kwargs['vmax'] = np.quantile(dtm, (.01, .99))

In [7]:
model = {}
load_tile(lidar_features[-1], tile_names[-1])

Traceback (most recent call last):
  File "/usr/lib/python3.9/site-packages/matplotlib/cbook/__init__.py", line 224, in process
    func(*args, **kwargs)
  File "/usr/lib/python3.9/site-packages/matplotlib/widgets.py", line 1555, in release
    self._release(event)
  File "/usr/lib/python3.9/site-packages/matplotlib/widgets.py", line 2112, in _release
    self.onselect(self.eventpress, self.eventrelease)
  File "<ipython-input-6-6d10fd3db2e6>", line 27, in line_select_callback
    filter_dtm()
  File "<ipython-input-6-6d10fd3db2e6>", line 84, in filter_dtm
    t = model['tree_cache']
KeyError: 'tree_cache'
<ipython-input-6-6d10fd3db2e6>:30: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for addit

HI!


## Interactive GUI

In [90]:
# "widget" or "qt", qt provide a snappier GUI
#%matplotlib widget
%matplotlib qt
plt.style.use('dark_background')

model.update({
    'ax_spectrum': None,
    'ax_dtm': None,
    'x': None,
    'y': None,
    'x1': 0,
    'x2': 0,
    'y1': 0,
    'y2': 0,
    'dtm_x1': 0,
    'dtm_x2': 0,
    'dtm_y1': 0,
    'dtm_y2': 0,
    'overlay': True,
    'pixel_mask': None,
})


def line_select_callback(eclick, erelease):
    model['x1'], model['y1'] = eclick.xdata, eclick.ydata
    model['x2'], model['y2'] = erelease.xdata, erelease.ydata
    filter_dtm()
    
def dtm_select_callback(eclick, erelease):
    model['dtm_y1'], model['dtm_x1'] = np.int(eclick.xdata), np.int(eclick.ydata)
    model['dtm_y2'], model['dtm_x2'] = np.int(erelease.xdata), np.int(erelease.ydata)
    filter_nodes()
    
def filter_nodes():
    x1, x2 = model['dtm_x1'], model['dtm_x2']
    y1, y2 = model['dtm_y1'], model['dtm_y2']
    pmask = np.zeros_like(model['im'], dtype=np.bool)
    pmask[x1:x2,y1:y2] = True
    model['pixel_mask'] = pmask
    model['highlight'] = True
    show_spectrum()
    
def show_spectrum():
    x, y = model['x'], model['y']
    x_log, y_log = model['x_log'], model['y_log']
    highlight = model['highlight']

    # Compute spectrum
    ps = sap.spectrum2d(model['tree_cache'], x, y, 200, 100, x_log, y_log)
    
    if highlight:
        node_mask = pixel_to_node(model['tree_cache'], model['pixel_mask']) if model['pixel_mask'] is not None else None
        ps_mask = spectrum2d(model['tree_cache'], x, y, 200, 100, x_log, y_log, node_mask=node_mask)
        ps[0][:] = ps_mask[0] / ps[0]

    # Display spectrum
    plt.sca(model['ax_spectrum'])
    plt.cla()
    sap.show_spectrum(*ps, log_scale=not highlight)
    plt.xlabel(x)
    plt.ylabel(y)
    plt.grid(which='minor', color='#BBBBBB', linestyle=':')
    plt.grid(True)
    
    plt.gcf().canvas.draw()


def filter_dtm():
    x1, x2 = model['x1'], model['x2']
    y1, y2 = model['y1'], model['y2']
    
    model['ax_dtm'].clear()

    # No filter
    if x1 == x2 == y1 == y2 == 0:
        if not model['overlay']:
            model['ax_dtm'].imshow(model['im'], **model['im_kwargs'])
        else:
            model['ax_dtm'].imshow(model['im'], **model['im_kwargs'])
            model['ax_dtm'].imshow(model['im_hs'], cmap=plt.cm.Greys, alpha=model['im_hs_alpha'])

        return
    
    # Filter
    t = model['tree_cache']
    X = t.get_attribute(model['x'])
    Y = t.get_attribute(model['y'])

    img = model['tree_cache'].reconstruct((X < x1) | (X > x2) | (Y < y1) | (Y > y2), filtering='subtractive')
    
    if not model['overlay']:
        model['ax_dtm'].imshow(img)
    else:
        model['ax_dtm'].imshow(model['im'], **model['im_kwargs'])
        model['ax_dtm'].imshow(model['im_hs'], cmap=plt.cm.Greys, alpha=model['im_hs_alpha'])
        model['ax_dtm'].contour(*model['im_mesh'], img, [model['tree_cache']._alt[-1]], colors='lime')

    plt.gcf().canvas.draw()

def spectrum_widget(tree=sap.MaxTree, x='area', y='compactness', x_log=True, y_log=False,
                    hillshade_overlay=True, highlight=False):
    # Update only toggle of hillshade_overlay
    if hillshade_overlay != model['overlay']:
        model['overlay'] = hillshade_overlay
        filter_dtm()
        return
    
    # Update model and tree computation if needed
    model.update({'x': x, 'y': y, 'x_log': x_log, 'y_log': y_log, 'highlight': highlight})
    if not 'tree_cache' in model or not isinstance(model['tree_cache'], tree):
        print('Computing the {} of the DTM...'.format(tree))
        model['tree_cache'] = tree(model['im'])
    
    show_spectrum()
    
    # Setup selector spectrum
    selector.rs = mpl.widgets.RectangleSelector(model['ax_spectrum'], line_select_callback,
       drawtype='box', useblit=True,
       button=[1, 3],  # don't use middle button
       minspanx=5, minspany=5,
       spancoords='pixels',
       rectprops = dict(facecolor=(0,1,0,.2), edgecolor=(0,1,0), fill=True, ls='--', lw=2),
       interactive=True)
    
    # Setup selector DTM
    selector_dtm.rs = mpl.widgets.RectangleSelector(model['ax_dtm'], dtm_select_callback,
       drawtype='box', useblit=True,
       button=[1, 3],  # don't use middle button
       minspanx=5, minspany=5,
       spancoords='pixels',
       rectprops = dict(facecolor=(1,1,0,.2), edgecolor=(1,1,0), fill=True, ls='--', lw=2),
       interactive=True)


plt.close()
fig = plt.figure('Spectrum', figsize=(18, 5), constrained_layout=True)
grid = mpl.gridspec.GridSpec(1, 3, fig)

model['ax_spectrum'] = fig.add_subplot(grid[:2])
model['ax_dtm'] = fig.add_subplot(grid[-1])

# Selectors
def selector(event):
    pass

def selector_dtm(event):
    pass


#plt.connect('key_press_event', selector)


filter_dtm()

ipw.interact(spectrum_widget, 
             tree=inspect.getmembers(sap.trees, lambda t: inspect.isclass(t) and issubclass(t, sap.Tree) and t != sap.Tree),
             x=sap.available_attributes().keys(),
             y=sap.available_attributes().keys())

interactive(children=(Dropdown(description='tree', index=1, options=(('AlphaTree', <class 'sap.trees.AlphaTree…

<function __main__.spectrum_widget(tree=<class 'sap.trees.MaxTree'>, x='area', y='compactness', x_log=True, y_log=False, hillshade_overlay=True, highlight=False)>

In [58]:
inspect.getmembers(sap.trees, lambda t: inspect.isclass(t) and issubclass(t, sap.Tree) and t != sap.Tree)

[('AlphaTree', sap.trees.AlphaTree),
 ('MaxTree', sap.trees.MaxTree),
 ('MinTree', sap.trees.MinTree),
 ('OmegaTree', sap.trees.OmegaTree),
 ('TosTree', sap.trees.TosTree)]

In [87]:
def load_tile():
    model['im'] = rio.open(get_tile(model['lidar_feature'].value, model['tile_name'].value)).read()[0]
    model['im_hs'] = ui8_clip(hillshades(model['im']), -1, 1)
    model['im_hs_alpha'] = ((model['im_hs'].astype(float) - 127) / 127) ** 2 * .4
    kwargs = {}
    kwargs['vmin'], kwargs['vmax'] = np.quantile(model['im'], (.01, .99))
    model['im_kwargs'] = kwargs
    model['im_mesh'] = np.meshgrid(np.arange(model['im'].shape[1]), np.arange(model['im'].shape[0]))

def load_tree():
    model['tree_cache'] = model['tree_type'].value(model['im'])

def reset_selections():
    model.update({
    'x1': 0,
    'x2': 0,
    'y1': 0,
    'y2': 0,
    'dtm_x1': 0,
    'dtm_x2': 0,
    'dtm_y1': 0,
    'dtm_y2': 0,
    'overlay': True,
    'highlight': False
})

In [99]:
model['lidar_feature'] = ipw.Dropdown(description='LiDAR feature', options=lidar_features)
model['tile_name'] = ipw.Dropdown(description='Tile ID', options=tile_names)
model['tree_type'] = ipw.Dropdown(description='Hierarchy', value=sap.trees.MaxTree, options=inspect.getmembers(sap.trees, lambda t: inspect.isclass(t) and issubclass(t, sap.Tree) and t != sap.Tree))
load_button = ipw.Button(description='Analyse', icon='rocket')

model['x'] = ipw.Dropdown(description='Attribute X', options=sap.available_attributes().keys())
model['y'] = ipw.Dropdown(description='Attribute Y', options=sap.available_attributes().keys())
model['x_log'] = ipw.Checkbox(description='X log')
model['y_log'] = ipw.Checkbox(description='Y log')
model['overlay'] = ipw.Checkbox(description='Filtering overlay')
model['highlight'] = ipw.Checkbox(description='Spectrum higlight')


def load_change(change):
    print('Loading tile...')
    load_tile()
    print('Loading tree...')
    load_tree()
    print('Loading complete')
    reset_selections()
    show_spectrum()
    filter_dtm()
    plt.show()

lidar_feature.observe(feature_change, names='value')
tile_name.observe(name_change, names='value')
tree_type.observe(tree_change, names='value')
load_button.on_click(load_change)

ipw.VBox([
    ipw.HBox([model['tile_name'], model['lidar_feature'], model['tree_type'] , load_button]),
    ipw.HBox([model['x'], model['x_log']]),
    ipw.HBox([model['y'], model['y_log']]),
    model['highlight'],
    model['overlay']
])